# Laboratorio 1.1
## Calcolare la similarità nelle definizioni dei 4 concetti del dataset



In [549]:
# python -m IPython notebook
from nltk import word_tokenize, SnowballStemmer
from nltk.corpus import stopwords, words
import string
import pandas as pd
import time
import random
start_time = time.time()

snow_stemmer = SnowballStemmer(language='english')

# Crea la variabile stop_words con le stop word e con la punteggiatura
stop_words = set(stopwords.words('english'))
stop_words.update(set(stopwords.words('italian')))
stop_words.update(set(string.punctuation))

def output_message(o=None):
    if o:
        print('\n ------------------------------------------------------------------------------------------------------------------\n Output - ' + str(o) + ' ------------------------------------------------------------------------------------------------------------------ ') 
        print("Tempo di esecuzione: %s secondi. " % round((time.time() - start_time),3))
    else:
        print('\n ------------------------------------------------------------------------------------------------------------------\n Tempo di esecuzione: %s secondi. ---------------------------------------------------------------------------------------------------------------- ' % round((time.time() - start_time),2))

# Pre-Processing
## 1. Definizione della funzione per l'estrazione delle informazioni dalla base di dati

In [550]:
media = {}           # Dictionary che conterrà la media aritmetica della lunghezza di ogni definizione per ogni concetto

def data_extraction(path='dataset/defs.csv'):
    if path == 'dataset/defs.csv':
        df = pd.read_csv(path, header=0)
        df = df.dropna()
        df.drop(['Partecipante'],axis=1,inplace=True)
        data = df.to_dict()

    elif 'dataset/db.csv':
        df = pd.read_csv(path, header=0, sep=',')
        data = df.values.tolist()

    return data

## 2. Definizione della funzione per la pulitura dell'input
La funzione restituirà un dictionary innestato di questo tipo `{Concetto: {utente 0: [definizione tokenizzata e stemmatizzata]}}`

In [551]:
def sort_indexes(data):
    defs = {}

    for concept in data.keys():
        i = 0
        defs.setdefault(concept,{})
        for index in data[concept]:
            defs[concept].setdefault(i, data[concept][index])
            i += 1
    return defs

In [552]:
def pre_processing(data):
    
    if type(data) == list:
        for element in range(len(data)):
            token = word_tokenize(data[element][0].lower())
            token = snow_stemmer.stem(token[0])
            del data[element]
            data.append(token)

    elif type(data) == dict:

        for names in data.keys():
            for index in data[names]:
                data[names][index] = word_tokenize(data[names][index].lower())
                data[names][index] = list(set([snow_stemmer.stem(word) for word in data[names][index] if word not in stop_words or word != "'s"]) - stop_words)

    return data

## Esecuzione delle funzioni dichiarate

In [553]:
start_time = time.time()
# Estrazione dei dati dei concetti in un dictionary
data = sort_indexes(data_extraction())

# Pre-processing dell'input
data = pre_processing(data)

In [554]:
output_message(data)


 ------------------------------------------------------------------------------------------------------------------
 Output - {'Courage': {0: ['feel', 'fear', 'despit', 'ani', 'properti', 'face', 'allow', 'situat'], 1: ['fear', 'unpleas', 'us', 'someth', 'make', 'face', 'scar', 'abil'], 2: ['fear', 'without', 'face', 'thing', 'abil'], 3: ['strength', 'inner', 'thaht', 'particular', 'face', 'allow', 'situat'], 4: ['abil', 'fear', 'control'], 5: ['fear', 'unpleas', 'someth', 'control', 'deal', 'abil'], 6: ['riski', 'take', 'fear', 'avoid', 'action', 'abil'], 7: ['take', 'choic', 'fear', 'action', 'abili', 'without', 'make'], 8: ['abl', 'fear', 'someth'], 9: ['abil', 'frighten', 'despit', 'someth'], 10: ['scare', 'peopl', 'abil', 'someth'], 11: ['feel', 'danger', 'us', 'face', 'allow', 'consid', 'situat'], 12: ['may', 'scari', 'abil', 'someth'], 13: ['abil', 'drastic', 'choic', 'make'], 14: ['abil', 'overcom', 'fear'], 15: ['risk', 'person', 'take', 'characterist'], 16: ['abl', 'danger',

# Calcolo della similarità
## 1. Definizione della funzione per il calcolo della lunghezza media delle definizioni di un concetto.
La lunghezza media delle definizioni è il rapporto tra la somma della lunghezza di tutte le definizioni e il numero delle definizioni
Output atteso: `{concetto0: 0.58, concetto1: 0.22}`


In [555]:
def average_length_computation(data_dictionary):
    average_length = {}

    for concept in data_dictionary.keys():

        average_words = []
        sentences = []

        for sentence in data_dictionary[concept]:
            new_sentence = word_tokenize(data_dictionary[concept][sentence])


            for token in new_sentence:
                average_words.append(1)
            
            sentences.append(1)
        
        average_length.setdefault(concept, sum(average_words) / len(sentences))

    return average_length      


In [556]:
print(average_length_computation(data_extraction()))

{'Courage': 9.333333333333334, 'Paper': 8.566666666666666, 'Apprehension': 7.533333333333333, 'Sharpener': 7.866666666666666}


## 2. Definizione della funzione per la sovrapposizione lessicale
Si intende definire la sovrapposizione lessicale tramite l'utilizzo della seguente struttura dati:
- `shared_words` sarà un dictionary annidato dove si terrà conto delle volte che una parola è stata utilizzata per ogni definizione di un concetto ecco un esempio del contenuto di questo array associativo: `{'Courage': { 'gatto': [0, 2, 0, 0, 0,..,0]}}` => Questo vuol dire che la parola gatto è stata usata due volte dall'utente in posizione 1.
- Utilizzando `shared_words` verrà calcolato il rapporto (`shared_words_rateo`) tra la frequenza delle parole utilizzate nelle varie definizioni e la quantità di definizioni per il concetto sul quale si sta iterando.

**Sovrapposizione lessicale** (`lexical_overlay`): Verrà restituito il numero delle "parole più utilizzate" nelle definizioni. Con "*parole più utilizzate*" si intendono le parole che sono comparse per almeno il 30% delle volte nelle definizioni del proprio concetto.


In [557]:
def lexical_overlay_computation(data_dictionary):
    defs = {}
    shared_words = {}
    lexical_overlay = {}
    relevant_words = {}

    # Creazione di un nuovo dictionary con gli indici ordinati (quello nella variabile "data" aveva alcuni indici senza definizione)
    for concept in data_dictionary.keys():
        i = 0
        defs.setdefault(concept,{})
        shared_words.setdefault(concept,{})
        for index in data_dictionary[concept]:
            defs[concept].setdefault(i, data_dictionary[concept][index])
            i += 1

    for concept in defs.keys():
        for index in defs[concept]:
            for word in defs[concept][index]:

                # Si avrà, per ogni parola, una lista di zeri composta da tanti elementi quante sono le definizioni
                # Si segna quante volte un utente utilizza una certa parola nella sua definizione
                if word not in shared_words[concept].keys():
                    shared_words[concept][word] = [0] * len(defs[concept].keys())

                shared_words[concept][word][index] += 1

    shared_words_rateo = {}
    # Si contano quanti utenti distinti hanno utilizzato una certa parola in una definizione / il totale delle definizioni
    for concept in shared_words.keys():
        if concept not in shared_words_rateo.keys():
            shared_words_rateo.setdefault(concept, {})

        for word in shared_words[concept]:
            if word not in shared_words_rateo[concept].keys():

                # Per ogni parola si fa il rapporto tra il numero di volte che quella parola è stata utilizzata in tutte le definizioni diviso il numero delle definizioni
                shared_words_rateo[concept].setdefault(word, sum(shared_words[concept][word]) / len(shared_words[concept][word]))
                if word not in relevant_words.keys():
                    relevant_words.setdefault(concept, [])
                
                relevant_words[concept].append([word, sum(shared_words[concept][word])])

            # Le parole più utilizzate vengono inserite nel dictionary di output
            if shared_words_rateo[concept][word] > 0.36:

                if word not in lexical_overlay.keys():
                    lexical_overlay.setdefault(concept, 0)
                lexical_overlay[concept] += 1

        lexical_overlay[concept] = lexical_overlay[concept]
    return [lexical_overlay, relevant_words, shared_words_rateo]

In [558]:
print(lexical_overlay_computation(data)[0])

{'Courage': 2, 'Paper': 3, 'Apprehension': 1, 'Sharpener': 5}


## 3. Definizione della funzione per il calcolo della similarità:
Per similarità si intende il rapporto tra sovrapposizione lessicale e lunghezza media delle definizioni.

In [559]:
def similarity_computation(data_dictionary, lexical_overlay, average_length):
    # Il calcolo della similarità è data dal rapporto tra sovrapposizione lessicale e lunghezza media delle definizioni
    similarity = {}
    for concept in data_dictionary.keys():
        similarity[concept] = round(lexical_overlay[concept] / average_length[concept], 4)
    return similarity

## Esecuzione delle funzioni dichiarate:

In [560]:
# Calcolo della lunghezza media delle definizioni
avg_len = average_length_computation(data_extraction())

# Calcolo della sovrapposizione lessicale
lex_overlay = lexical_overlay_computation(data)[0]

# Calcolo della similarità
similarity = similarity_computation(data, lex_overlay, avg_len)

In [561]:
output_message(similarity)


 ------------------------------------------------------------------------------------------------------------------
 Output - {'Courage': 0.2143, 'Paper': 0.3502, 'Apprehension': 0.1327, 'Sharpener': 0.6356} ------------------------------------------------------------------------------------------------------------------ 
Tempo di esecuzione: 0.226 secondi. 


# Risultati laboratorio 1.1
Di seguito una lista con gli di output del primo esercizio sul calcolo numerico della similarity:
- Coraggio: 0.0291
- Carta: 0.0286
- Inquietudine: 0.0278
- Temperino: 0.0527

___

# Laboratorio 1.2
## Similarity Explanation: spiegazione della similarità numerica.
Si intende spiegare la similarità numerica restituendo in output una lista con le 5 parole maggiormente rilevanti per ogni concetto.
Le 5 parole sono state precedentemente calcolate con la funzione `lexical_overlay_computation()`. La funzione `get_relevant_words` permette di scegliere se ricevere in output il dictionary con tutte le parole più usate o una lista con le 5 parole più usate, o ancora, permette di visualizzare l'output in una tabella

In [562]:
from operator import itemgetter
def get_relevant_words(dictionary_of_words, only_best_words=1, number_of_words=6, display=0):
    output = []
    # Dictionary contenente le parole più rilevanti
    relevant_words = lexical_overlay_computation(dictionary_of_words)[1]
    for concept in relevant_words.keys():
        i = 0
        # Le parole vengono all'interno del dictionary vengono riordinate
        relevant_words[concept] = sorted(relevant_words[concept], key=itemgetter(1), reverse=True)
        # Se il parametro viene asserito allora viene stampata una tabella con le 5 parole più usate per ogni concetto

        # Se return best è asserito a zero la funzione non ritornerà le 5 parole più usate
        if only_best_words != 0:
            # Se display è asserito viene stampata una tabella
            if display != 0:
                print(f'\n {concept}')
                print(f'Freq - \t Token')
            output.append(concept)

            for tuple in relevant_words[concept]:
                # stamperà i 5 valori più alti
                if i < number_of_words:
                    pass
                    output.append([tuple[1], tuple[0]])

                    # Se display è asserito viene stampata una tabella
                    if display != 0:
                        print(f'{tuple[1]} \t - \t {tuple[0]}')

                    i += 1
    if output:
        return output
    else:
        return relevant_words

# Esecuzione della funzione dichiarata

In [563]:
# In output una lista con le 5 parole più usate
relevant_words = get_relevant_words(data)



# Laboratorio 1.3
## Word Sense Induction
Si contrappone al Word Sense Disambiguation che è un problema computazionale aperto in cui si deve riconoscere il **senso** di una parola in una frase, siccome una parola può essere utilizzata con accezioni differenti.
Il ***Word Sense Induction*** è invece basato su un meccanismo dove si uniscono due parole (creando una pseudo-word) e si da uno score se quando si itera sul corpus si incontra una delle componenti della pseudoword. Lo score può essere positivo se si ci riferisce a una componente e negativo se ci si riferisce alla seconda componente.

In [564]:
# Restituisce una lista con tutti i token distinte utilizzate
def get_tokens(corpus): 
    words = []
    data = pre_processing(corpus)

    if type(corpus) == dict:
        for concept in data.keys():
            for sentence in corpus[concept]:
                for token in corpus[concept][sentence]:
                    if token != "'s":
                        words.append(token)

    elif type(data) == list:
        for element in data:
            if element[0] != "'s":
                words.append(element[0])

    return list(set(words))

In [565]:
print(get_tokens(data_extraction()))

['may', 'understand', 'smooth', 'overcom', 'worri', 'end', 'inner', 'done', 'univers', 'wood', 'scar', 'handwrit', 'work', 'uncofort', 'return', 'constant', 'tool', 'medium', 'product', 'inform', 'moral', 'cut', 'kind', 'sharpen', 'abil', 'take', 'sheet', 'fear', 'act', 'veri', 'use', 'stationeri', 'someth', 'unaccommod', 'thaht', 'without', 'thing', 'type', 'uneas', 'cellulos', 'flat', 'awe', 'communic', 'avoid', 'usual', 'laid', 'pencil', 'write', 'state', 'especi', 'drastic', 'context', 'negat', 'strength', 'scare', 'creat', 'make', 'face', 'easi', 'loss', 'order', 'peopl', 'behavior', 'object', 'print', 'discomfort', 'nervous', 'sever', 'pathway', 'avail', 'sharpner', 'status', 'mind', 'brutto', 'surfac', 'sharp', 'lightweight', 'riski', 'frighten', 'mental', 'tip', 'differ', 'restless', 'paura', 'perform', 'withstand', 'graphit', 'caus', 'littl', 'easili', 'abl', 'piec', 'note', 'devic', 'veget', 'danger', 'screen', 'someon', 'qualiti', 'compos', 'go', 'mood', 'subject', 'qualcosa

In [566]:
# Restituisce un dictionary con le pseudo-words come chiavi e 0 come valori
def generate_pseudo_words(corpus):
    list_of_tokens = get_tokens(corpus)
    pseudo_words = {}
    scores = {}
    
    for token in range(0, len(list_of_tokens), 2):
        try:
            pseudo_word = list_of_tokens[token] + list_of_tokens[token + 1]
            scores.setdefault(pseudo_word, 0)
            pseudo_words.setdefault(pseudo_word, [list_of_tokens[token], list_of_tokens[token + 1]])

        except IndexError:
            continue
        
    return [scores, pseudo_words]

In [567]:
#print(generate_pseudo_words(data_extraction('dataset/db.csv'))[1])

In [568]:
# Restituisce un nuovo corpus con al posto di alcuni token i token con le pseudo-words, e in più restituisce anche una lista associativa con le pseudo-words e il loro score
def substitute_pseudo_words(corpus, corpus_to_substitute=None):
    corpus = pre_processing(corpus)
    corpus_to_substitute = pre_processing(corpus_to_substitute)
    new_corpus = {}
    pseudo_words_dictionary = generate_pseudo_words(corpus)[0]
    pseudo_words_map = generate_pseudo_words(corpus)[1]


    if type(corpus) == dict:

        for concept in corpus.keys():
            new_corpus.setdefault(concept, {})
            
            for definition_number in corpus[concept]: 

                if definition_number not in new_corpus[concept].keys():
                    new_corpus[concept].setdefault(definition_number, [])
                    
                    
                for token in corpus[concept][definition_number]:
                    keys = list(pseudo_words_dictionary.keys())
                    combined = '\t'.join(keys)
                    if token in combined:
                        pseudo_word = [pseudo_word for pseudo_word in keys if token in pseudo_word][0]

                        # Se la parola la prima parola che compone la pseudo-word è contenuta nella pseudo-word allora si aggiunge 1
                        if token in pseudo_words_map[pseudo_word][0]:
                            pseudo_words_dictionary[pseudo_word] += 1
                        else: 
                            pseudo_words_dictionary[pseudo_word] -= 1   

                        if pseudo_word != '':
                            token = token.replace(token, pseudo_word)

                    new_corpus[concept][definition_number].append(token)

    elif type(corpus) == list:
        for element in corpus:
            token = element[0]
            keys = list(pseudo_words_dictionary.keys())
            combined = '\t'.join(keys)
            if token in combined:
                pseudo_word = [pseudo_word for pseudo_word in keys if token in pseudo_word][0]

                # Se la parola la prima parola che compone la pseudo-word è contenuta nella pseudo-word allora si aggiunge 1
                try:
                    if token in pseudo_words_map[pseudo_word][0]:
                        pseudo_words_dictionary[pseudo_word] += 1

                except KeyError:
                    pseudo_words_dictionary.setdefault(pseudo_word, 1)

                try:
                    if token in pseudo_words_map[pseudo_word][1]:
                        pseudo_words_dictionary[pseudo_word] -= 1

                except KeyError:
                    pseudo_words_dictionary.setdefault(pseudo_word, -1)

                if pseudo_word != '':
                    token = token.replace(token, pseudo_word)

            for concept in corpus_to_substitute.keys():
                if concept not in new_corpus.keys():
                    new_corpus.setdefault(concept, {})


                for definition_number in corpus_to_substitute[concept]:
                    new_definition = []
                    for token in corpus_to_substitute[concept][definition_number]:
                        print(token)
                        if token in pseudo_word[0:len(token)]:
                            print(f"{token} - {pseudo_word[0:len(token)]}")

                            token = token.replace(token, pseudo_word)
                            print(token)
                            new_definition.append(token)
                    new_corpus[concept].setdefault(definition_number, new_definition)

    return [new_corpus, pseudo_words_dictionary]            

In [569]:
substitute_pseudo_words(data_extraction('dataset/db.csv'), data_extraction())

feel
fear
despit
ani
properti
face
allow
situat
fear
unpleas
us
someth
make
face
scar
abil
fear
without
face
thing
abil
strength
inner
thaht
particular
face
allow
situat
abil
fear
control
fear
unpleas
someth
control
deal
abil
riski
take
fear
avoid
action
abil
take
choic
fear
action
abili
without
make
abl
fear
someth
abil
frighten
despit
someth
scare
peopl
abil
someth
feel
danger
us
face
allow
consid
situat
may
scari
abil
someth
abil
drastic
choic
make
abil
overcom
fear
risk
person
take
characterist
abl
danger
scare
qualiti
thing
general
hero
behavior
typic
difficult
situat
abil
face
abil
peopl
fear
someth
face
strength
difficult
mind
allow
situat
's
fear
one
face
abil
abil
block
fear
beyond
emot
expect
someon
go
allow
fear
despit
danger
act
perform
abil
fear
danger
strength
mental
ventur
persever
withstand
difficulti
moral
fear
scare
resist
provok
abil
situat
abil
overcom
fear
fear
overcom
difficult
face
abil
situat
abl
scare
aptitud
human
make
fold
cellulos
written
materi
cut
tree
con

[{'Courage': {0: [],
   1: [],
   2: [],
   4: [],
   5: [],
   6: [],
   7: [],
   8: [],
   9: [],
   10: [],
   11: [],
   13: [],
   14: [],
   15: [],
   16: [],
   17: [],
   18: [],
   19: [],
   20: [],
   21: [],
   22: [],
   23: [],
   24: [],
   25: [],
   26: [],
   27: [],
   28: [],
   29: [],
   30: [],
   31: []},
  'Paper': {0: [],
   1: [],
   2: [],
   4: [],
   5: [],
   6: [],
   7: [],
   8: [],
   9: [],
   10: [],
   11: [],
   13: [],
   14: [],
   15: [],
   16: [],
   17: [],
   18: [],
   19: [],
   20: [],
   21: [],
   22: [],
   23: [],
   24: [],
   25: [],
   26: [],
   27: [],
   28: [],
   29: [],
   30: [],
   31: []},
  'Apprehension': {0: [],
   1: [],
   2: [],
   4: [],
   5: [],
   6: [],
   7: [],
   8: [],
   9: [],
   10: [],
   11: [],
   13: [],
   14: [],
   15: [],
   16: [],
   17: [],
   18: [],
   19: [],
   20: [],
   21: [],
   22: [],
   23: [],
   24: [],
   25: [],
   26: [],
   27: [],
   28: [],
   29: [],
   30: [],
   31: []}

In [570]:
print(substitute_pseudo_words(data_extraction('dataset/db.csv'))[1])

AttributeError: 'NoneType' object has no attribute 'keys'

In [ ]:
# Score to probability
def score_converter(score, scores_dictionary):
    temp = []
    rate = 0.00

    for value in scores_dictionary.values():
        temp.append(value)
    
    pos_max_score = max(temp)
    neg_max_score = min(temp)

    # Percentuale di quanto lo score è positivo (1.0 se è uguale al massimo)
    if score > 0:
        rate = score / pos_max_score

    elif score < 0:
        # Percentuale di quanto lo score è negativo (1.0 se è uguale al massimo)
        rate = score / neg_max_score
        
    rate = round(rate, 2)
    return rate


In [ ]:
score_converter(-10, substitute_pseudo_words(data_extraction())[1])

AttributeError: 'list' object has no attribute 'lower'

In [ ]:
def wsi(target_corpus, scores, pseudo_words):

    for concept in target_corpus.keys():
        for index in target_corpus[concept]:
            for token_index in range(len(target_corpus[concept][index])):
                token = target_corpus[concept][index][token_index]

                if token in scores.keys():
                    pseudo_word = pseudo_words[token]

                    score = scores[token]

                    if score > 0:
                        target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[0]) 

                    elif score == 0:
                        random_index = random.randint(0, 1)
                        target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[random_index]) 

                    else: 
                        target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[1]) 

    return target_corpus

In [ ]:
def wsi2(target_corpus, scores, pseudo_words):

    for concept in target_corpus.keys():
        for index in target_corpus[concept]:
            for token_index in range(len(target_corpus[concept][index])):
                token = target_corpus[concept][index][token_index]

                if token in scores.keys():
                    pseudo_word = pseudo_words[token]

                    score = scores[token]

                    rate = score_converter(score, substitute_pseudo_words(data_extraction())[1])
                    rnd = random.randint(0.00, 1.00)

                    if score > 0:
                        if rate > rnd:
                            target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[0]) 
                        else:
                            target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[1]) 

                    elif score == 0:
                        random_index = random.randint(0, 1)
                        target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[random_index]) 

                    else: 
                        if rate > rnd:
                            target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[0]) 
                        else:
                            target_corpus[concept][index][token_index] = token.replace(token, pseudo_word[1]) 

    return target_corpus

In [ ]:
def eval(wsi_corpus, real_corpus):
    real_corpus = pre_processing(real_corpus)
    right_previsions = 0
    total = 0
    for concept in real_corpus.keys():
        for index in real_corpus[concept]:
            for token_index in range(len(real_corpus[concept][index])):
                token = real_corpus[concept][index][token_index]
                
                if token == wsi_corpus[concept][index][token_index]:
                    right_previsions += 1
                    
                total += 1
    accuracy = right_previsions / total

    return accuracy

In [ ]:
# Main
input_corpus = substitute_pseudo_words(data_extraction())[0]

scores = substitute_pseudo_words(data_extraction())[1]

pseudo_words = generate_pseudo_words()[1]

wsi_corpus = wsi(input_corpus, scores, pseudo_words)

accuracy = eval(wsi_corpus, data_extraction())

In [ ]:
print(round(accuracy, 2))

0.89


# Laboratorio 1.4
Scegliere un verbo transitivo con almeno 2 argomenti, recuperare un corpus di $n$ istanze (>1000) in cui esso viene usato. Effetuare parsing e disambiguazione, usare i super sense di wordnet sugli argomenti nel verbo scelto, aggregare i risultati, calcolare le frequenze, stampare i cluster semantici ottenuti.

In [ ]:
data_extraction('dataset/db.csv')

[['coronavirus'],
 ['archived'],
 ['pandemic'],
 ['covid'],
 ['wayback'],
 ['displaystyle'],
 ['lockdown'],
 ['distancing'],
 ['naruto'],
 ['retrieve'],
 ['sasuke'],
 ['xena'],
 ['biden'],
 ['من'],
 ['maint'],
 ['في'],
 ['gabrielle'],
 ['cs1'],
 ['kurama'],
 ['agrave'],
 ['wager'],
 ['hemorrhoid'],
 ['fn'],
 ['plurality'],
 ['isbn'],
 ['tags'],
 ['rcw'],
 ['vin'],
 ['hiei'],
 ['oclc'],
 ['rafi'],
 ['ó'],
 ['romanize'],
 ['kakashi'],
 ['faramir'],
 ['liz'],
 ['vicodin'],
 ['yusuke'],
 ['ghostwriter'],
 ['abilify'],
 ['phentermine'],
 ['jackpot'],
 ['ats'],
 ['embodiment'],
 ['fioricet'],
 ['contrib'],
 ['ultram'],
 ['alford'],
 ['itachi'],
 ['née'],
 ['carisoprodol'],
 ['authors'],
 ['sars-cov-2'],
 ['footballer'],
 ['kashmir'],
 ['egrave'],
 ['poker'],
 ['tenuate'],
 ['collett'],
 ['ufc'],
 ['predetermine'],
 ['isabel'],
 ['snape'],
 ['allmusic'],
 ['nsk'],
 ['emini'],
 ['dafa'],
 ['hydrocodone'],
 ['che'],
 ['spock'],
 ['rsquo'],
 ['indicia'],
 ['argent'],
 ['blackjack'],
 ['neji'],
 